In [ ]:
%matplotlib inline


# ISI and CV Analysis with Optimized Descending Drive

This example demonstrates **spike train analysis** using optimized descending drive parameters
from previous optimization studies. It extracts inter-spike interval (ISI) and coefficient of
variation (CV) statistics during realistic trapezoidal contraction patterns.

<div class="alert alert-info"><h4>Note</h4><p>**Analysis workflow**:

    1. Load optimized DD parameters from baseline or force-specific optimization
    2. Generate trapezoidal drive pattern (ramp-up, plateau, ramp-down)
    3. Simulate motor neuron spike trains with optimized network
    4. Extract ISI/CV statistics during plateau phase
    5. Visualize firing patterns and instantaneous discharge rates</p></div>

.. important::
    **Prerequisites**: This example requires results from previous optimizations:

    - **Baseline mode**: Run ``00_optimize_dd_for_target_firing_rate.py`` first
    - **Force mode**: Run ``02_optimize_dd_for_target_force.py`` for specific MVC level
    - Loads network structure and drive parameters from saved results

**Trapezoidal Contraction**: Simulates realistic voluntary isometric contractions with:

- **Ramp-up phase**: Linear increase from rest to target force (1 second)
- **Plateau phase**: Sustained contraction at target level (2 seconds)
- **Ramp-down phase**: Linear decrease back to rest (1 second)
- **Rest periods**: Baseline activity before and after contraction (1 second each)

**ISI/CV Metrics**: Quantify firing variability and regularity for motor control studies.


## Import Libraries



In [ ]:
import os

os.environ["MPLBACKEND"] = "Agg"
if "DISPLAY" in os.environ:
    del os.environ["DISPLAY"]

import itertools
import json
import warnings
from pathlib import Path

import elephant
import joblib
import numpy as np
import quantities as pq
from matplotlib import pyplot as plt
from neo import AnalogSignal, Block, Segment, SpikeTrain
from neuron import h
from tqdm import tqdm

from myogen import set_random_seed
from myogen.simulator import RecruitmentThresholds
from myogen.simulator.neuron import Network
from myogen.simulator.neuron.populations import AlphaMN__Pool, DescendingDrive__Pool
from myogen.utils.helper import calculate_firing_rate_statistics
from myogen.utils.nmodl import load_nmodl_mechanisms

warnings.filterwarnings("ignore")
plt.style.use("fivethirtyeight")

## Configuration

Set analysis parameters and specify which optimization results to load.



In [ ]:
# Random seed for reproducibility
set_random_seed(42)

# Study parameters
MUSCLE_TYPE = "TEST"  # Muscle identifier
MVC_LEVEL = 30  # MVC percentage (used for file naming)
STUDY_PREFIX = "TEST_"  # Prefix for output files

# Optimization mode selection
USE_BASELINE_OPTIMIZATION = True  # True = baseline FR optimization, False = force optimization
TARGET_FORCE_PCT = 30  # Force level if using force optimization

# Simulation parameters
TIMESTEP__ms = 0.1
N_MOTOR_UNITS = 100

# Trapezoidal contraction timing
RAMP_UP_DURATION__ms = 1000  # 1 second ramp-up
PLATEAU_DURATION__ms = 2000  # 2 second plateau
RAMP_DOWN_DURATION__ms = 1000  # 1 second ramp-down
REST_BEFORE__ms = 1000  # 1 second rest before
REST_AFTER__ms = 1000  # 1 second rest after

# Directories - use project root to share across examples
# Handle both manual execution and Sphinx Gallery (where __file__ is not defined)
try:
    _script_dir = Path(__file__).parent
except NameError:
    _script_dir = Path.cwd()
RESULTS_DIR = _script_dir.parent.parent / "results"
RESULTS_DIR.mkdir(exist_ok=True, parents=True)

## Load Optimized DD Parameters

Load network parameters from previous optimization studies.



In [ ]:
print(f"\n{'=' * 80}")
print("LOADING OPTIMIZED DD PARAMETERS")
print(f"{'=' * 80}\n")

if USE_BASELINE_OPTIMIZATION:
    # Load from baseline firing rate optimization
    OPTIMIZATION_RESULTS_DIR = _script_dir.parent.parent / "results" / "dd_optimization"
    PARAMS_FILE = OPTIMIZATION_RESULTS_DIR / "dd_optimized_params.json"  # No prefix for baseline

    print("Loading from BASELINE firing rate optimization...")

    # Fallback to static example data if dynamic results don't exist
    STATIC_DATA_DIR = _script_dir.parent / "data" / "dd_optimization"
    STATIC_PARAMS_FILE = STATIC_DATA_DIR / "dd_optimized_params.json"

    if PARAMS_FILE.exists():
        print(f"  ✓ Using dynamic results from: {PARAMS_FILE.relative_to(_script_dir.parent.parent)}")
    elif STATIC_PARAMS_FILE.exists():
        print(f"  ✓ Using static example data from: {STATIC_PARAMS_FILE.relative_to(_script_dir.parent.parent)}")
        PARAMS_FILE = STATIC_PARAMS_FILE
    else:
        raise FileNotFoundError(
            f"Baseline optimization results not found.\n"
            f"  Tried: {PARAMS_FILE}\n"
            f"  Tried: {STATIC_PARAMS_FILE}\n"
            "Please run optimize_dd_for_target_firing_rate.py first or check examples/data/"
        )

    with open(PARAMS_FILE, "r") as f:
        optimization_results = json.load(f)

    # Extract DD parameters from best firing rate match
    dd_params = optimization_results["best_trial"]
    source_description = "baseline FR optimization"

else:
    # Load from force-specific optimization
    OPTIMIZATION_RESULTS_DIR = _script_dir.parent.parent / "results" / "force_optimization"

    # List available force optimization files
    if OPTIMIZATION_RESULTS_DIR.exists():
        available_files = sorted(
            OPTIMIZATION_RESULTS_DIR.glob(f"{STUDY_PREFIX}dd_optimized_params_force_*pct.json")
        )
        if available_files:
            print("Available force optimization results:")
            for i, file in enumerate(available_files):
                # Extract percentage from filename
                pct = file.stem.split("_")[-1].replace("pct", "")
                print(f"  {i + 1}. {pct}% MVC - {file.name}")
            print()

    PARAMS_FILE = (
        OPTIMIZATION_RESULTS_DIR
        / f"{STUDY_PREFIX}dd_optimized_params_force_{int(TARGET_FORCE_PCT)}pct.json"
    )

    print(f"Loading from FORCE-SPECIFIC optimization ({TARGET_FORCE_PCT}% MVC)...")

    if not PARAMS_FILE.exists():
        raise FileNotFoundError(
            f"Force optimization results not found at {PARAMS_FILE}.\n"
            f"Please run: python optimize_dd_for_target_force.py --target-force-pct {TARGET_FORCE_PCT}"
        )

    with open(PARAMS_FILE, "r") as f:
        optimization_results = json.load(f)

    # Extract DD parameters from force optimization results
    dd_params = optimization_results["dd_parameters"]
    source_description = f"{TARGET_FORCE_PCT}% MVC force optimization"

# Extract common DD parameters
N_DD_NEURONS = dd_params["dd_neurons"]
DD_CONNECTION_PROBABILITY = dd_params["conn_probability"]
DD_PEAK__Hz = dd_params["dd_drive__Hz"]
DD_SHAPE_PARAMETER = dd_params["gamma_shape"]
DD_SYNAPTIC_WEIGHT = dd_params.get("synaptic_weight", 0.05)

# Load Gfluctdv settings if present
GFLUCTDV_ENABLED = optimization_results.get("gfluctdv_enabled", False)
GFLUCTDV_NOISE_AMPLITUDE = dd_params.get("gfluctdv_noise_amplitude", None)

print(f"\n(OK) Loaded from: {source_description}")
print(f"  Source file: {PARAMS_FILE.name}")
print("\nOptimized DD parameters:")
print(f"\tDD neurons: {N_DD_NEURONS}")
print(f"\tConn probability: {DD_CONNECTION_PROBABILITY:.3f}")
print(f"\tSynaptic weight: {DD_SYNAPTIC_WEIGHT:.4f} uS")
print(f"\tDD drive level: {DD_PEAK__Hz:.2f} Hz")
print(f"\tGamma shape: {DD_SHAPE_PARAMETER:.2f} (CV={1 / DD_SHAPE_PARAMETER**0.5:.3f})")
if GFLUCTDV_ENABLED:
    print(f"\tGfluctdv: ENABLED (noise={GFLUCTDV_NOISE_AMPLITUDE:.2e} S/cm²)")

## Initialize NEURON and Create Motor Neuron Pool

Setup NEURON simulator and create the motor neuron population.



In [ ]:
load_nmodl_mechanisms()
h.secondorder = 2  # Crank-Nicolson integration

recruitment_thresholds, _ = RecruitmentThresholds(
    N=N_MOTOR_UNITS,
    recruitment_range__ratio=100,
    deluca__slope=5,
    konstantin__max_threshold__ratio=1.0,
    mode="combined",
)

motor_neuron_pool = AlphaMN__Pool(
    recruitment_thresholds__array=recruitment_thresholds,
    config_file="alpha_mn_default.yaml",
)

# Apply Gfluctdv if it was enabled during optimization
if GFLUCTDV_ENABLED and GFLUCTDV_NOISE_AMPLITUDE is not None:
    print("\nApplying Gfluctdv to motor neurons (matching DD optimization)...")
    print(f"\tNoise amplitude: {GFLUCTDV_NOISE_AMPLITUDE:.2e} S/cm²")
    for cell in motor_neuron_pool:
        cell.insert_Gfluctdv()
        for d in cell.dend:
            d.std_e_Gfluctdv = GFLUCTDV_NOISE_AMPLITUDE
            d.std_i_Gfluctdv = GFLUCTDV_NOISE_AMPLITUDE
else:
    print("\nGfluctdv NOT enabled (following DD optimization settings)")

# Create descending drive pool with optimized parameters
descending_drive_pool = DescendingDrive__Pool(
    n=N_DD_NEURONS,
    timestep__ms=TIMESTEP__ms * pq.ms,
    process_type="gamma",
    shape=DD_SHAPE_PARAMETER,
)

## Generate Trapezoidal Drive Pattern

Create a **trapezoidal ramp contraction pattern** that represents realistic
voluntary isometric contractions. This pattern has 4 phases:
1. **Ramp-up**: Linear increase from baseline to peak
2. **Plateau**: Sustained peak drive level
3. **Ramp-down**: Linear decrease from peak to baseline
4. **Rest**: Baseline activity

This is a common experimental paradigm used in motor control studies.



In [ ]:
# Calculate total simulation time
simulation_time = (
    REST_BEFORE__ms
    + RAMP_UP_DURATION__ms
    + PLATEAU_DURATION__ms
    + RAMP_DOWN_DURATION__ms
    + REST_AFTER__ms
)
time_points = int(simulation_time / TIMESTEP__ms)

# Drive parameters
dd_baseline__Hz = 0.0  # Baseline drive during rest
dd_peak__Hz = DD_PEAK__Hz  # Peak drive from optimization

# Calculate phase boundaries
trapezoid_start = REST_BEFORE__ms
ramp_up_end = trapezoid_start + RAMP_UP_DURATION__ms
plateau_end = ramp_up_end + PLATEAU_DURATION__ms
ramp_down_end = plateau_end + RAMP_DOWN_DURATION__ms

# Create time array
time_array = np.linspace(0, simulation_time, time_points)

# Initialize drive signal (all baseline)
trapezoid_drive = np.ones(time_points) * dd_baseline__Hz

for i, t in enumerate(time_array):
    if t < trapezoid_start:
        # Phase 0: Rest before
        trapezoid_drive[i] = dd_baseline__Hz
    elif t < ramp_up_end:
        # Phase 1: Ramp up
        elapsed = t - trapezoid_start
        trapezoid_drive[i] = dd_baseline__Hz + (dd_peak__Hz - dd_baseline__Hz) * (
            elapsed / RAMP_UP_DURATION__ms
        )
    elif t < plateau_end:
        # Phase 2: Plateau
        trapezoid_drive[i] = dd_peak__Hz
    elif t < ramp_down_end:
        # Phase 3: Ramp down
        elapsed = t - plateau_end
        trapezoid_drive[i] = dd_peak__Hz - (dd_peak__Hz - dd_baseline__Hz) * (
            elapsed / RAMP_DOWN_DURATION__ms
        )
    else:
        # Phase 4: Rest after
        trapezoid_drive[i] = dd_baseline__Hz

# Create AnalogSignal for drive pattern
trapezoid_drive__signal = AnalogSignal(
    signal=trapezoid_drive,
    units=pq.Hz,
    sampling_period=(TIMESTEP__ms * pq.ms).rescale(pq.s),
)

joblib.dump(trapezoid_drive__signal, RESULTS_DIR / f"{STUDY_PREFIX}trapezoid_drive_pattern.pkl")
print(f"\nTrapezoidal drive pattern (using optimized DD drive of {dd_peak__Hz:.2f} Hz):")
print(f"\tRest before: 0 - {trapezoid_start} ms ({dd_baseline__Hz} Hz)")
print(f"\tRamp up: {trapezoid_start} - {ramp_up_end} ms ({dd_baseline__Hz} → {dd_peak__Hz:.2f} Hz)")
print(
    f"\tPlateau: {ramp_up_end} - {plateau_end} ms ({dd_peak__Hz:.2f} Hz, center at {(ramp_up_end + plateau_end) / 2:.0f}ms)"
)
print(f"\tRamp down: {plateau_end} - {ramp_down_end} ms ({dd_peak__Hz:.2f} → {dd_baseline__Hz} Hz)")
print(f"\tRest after: {ramp_down_end} - {simulation_time} ms ({dd_baseline__Hz} Hz)")
print("\nUsing optimized DD parameters:")
print(f"\tGamma shape: {DD_SHAPE_PARAMETER:.2f} (CV={1 / DD_SHAPE_PARAMETER**0.5:.3f})")
print(f"\tConnection probability: {DD_CONNECTION_PROBABILITY:.3f}")

## Build Network and Connect Populations

Create synaptic connections using optimized parameters.



In [ ]:
network = Network({"DD": descending_drive_pool, "aMN": motor_neuron_pool})

# Connect DD neurons to motor neurons with optimized synaptic parameters
network.connect(
    source="DD",
    target="aMN",
    probability=DD_CONNECTION_PROBABILITY,
    weight__uS=DD_SYNAPTIC_WEIGHT * pq.uS,
)

# Set up external input to DD population
network.connect_from_external(source="cortical_input", target="DD", weight__uS=1.0 * pq.uS)
# Get NetCons for manual DD stimulation
dd_netcons = network.get_netcons("cortical_input", "DD")

## Setup Spike Recording

To record spikes, we need to manually set up spike detection for the motor neurons
and track spike times for the DD neurons.




In [ ]:
# Manual spike tracking for DD neurons (they use Poisson processes)
dd_spike_times = [[] for _ in range(len(descending_drive_pool))]

# Record spikes from motor neurons
mn_spike_recorders = []
for cell in motor_neuron_pool:
    spike_recorder = h.Vector()
    nc = h.NetCon(cell.soma(0.5)._ref_v, None, sec=cell.soma)
    nc.threshold = 50  # Standard threshold for motor neurons
    nc.record(spike_recorder)
    mn_spike_recorders.append(spike_recorder)

## Run Simulation

Execute the NEURON simulation with trapezoidal drive pattern.



In [ ]:
h.load_file("stdrun.hoc")
h.dt = TIMESTEP__ms
h.tstop = simulation_time

# Initialize voltages for all pools
for section, voltage in itertools.chain.from_iterable(
    zip(*pool.get_initialization_data()) for pool in [motor_neuron_pool, descending_drive_pool]
):
    section.v = voltage


h.finitialize()

step_counter = 0
with tqdm(
    total=simulation_time,
    desc="Running simulation",
    unit="ms",
    bar_format="{l_bar}{bar}| {n:.2f}/{total:.2f} ms [{elapsed}<{remaining}, {rate_fmt}]",
) as pbar:
    while h.t < h.tstop:
        current_drive = trapezoid_drive__signal[min(step_counter, len(trapezoid_drive__signal) - 1)]

        # Drive DD neurons with current input level
        for dd_cell in descending_drive_pool:
            if dd_cell.integrate(current_drive):
                spike_time = h.t + 1
                dd_spike_times[dd_cell.pool__ID].append(spike_time)

                if spike_time < h.tstop:
                    dd_netcons[dd_cell.pool__ID].event(spike_time)

        h.fadvance()
        step_counter += 1
        pbar.update(TIMESTEP__ms)

## Convert Spike Data to Neo Format

Process recorded spike times into Neo data structures.



In [ ]:
spike_train_block = Block(name="Trapezoidal Contraction Spike Trains")

dd_segment = Segment(name="Descending Drive")
dd_segment.spiketrains = [
    SpikeTrain(
        (spike_times * pq.ms).rescale(pq.s),
        t_stop=(simulation_time * pq.ms).rescale(pq.s),
        sampling_rate=(1 / (h.dt * pq.ms)).rescale(pq.Hz),
        sampling_period=(h.dt * pq.ms).rescale(pq.s),
        name=f"DD_{i}",
    )
    for i, spike_times in enumerate(dd_spike_times)
]

mn_segment = Segment(name="Motor Neurons")
mn_segment.spiketrains = [
    SpikeTrain(
        (recorder.as_numpy() * pq.ms).rescale(pq.s),
        t_stop=(simulation_time * pq.ms).rescale(pq.s),
        sampling_rate=(1 / (h.dt * pq.ms)).rescale(pq.Hz),
        sampling_period=(h.dt * pq.ms).rescale(pq.s),
        name=f"MN_{i}",
    )
    for i, recorder in enumerate(mn_spike_recorders)
]

# Save motor neuron spike trains
spike_train_block.segments.append(mn_segment)

joblib.dump(spike_train_block, RESULTS_DIR / f"{STUDY_PREFIX}trapezoidal_spike_trains.pkl")

## Calculate Firing Rate Statistics




In [ ]:
print("\nFiring rate analysis:")

# Calculate DD firing rates
dd_firing_rates = np.array(
    [
        elephant.statistics.mean_firing_rate(st__s.time_slice(st__s.min(), st__s.max()))
        for st__s in dd_segment.spiketrains
        if len(st__s) > 0
    ]
)

# Calculate MN firing rates
mn_firing_rates = np.array(
    [
        elephant.statistics.mean_firing_rate(st__s.time_slice(st__s.min(), st__s.max()))
        for st__s in mn_segment.spiketrains
        if len(st__s) > 0
    ]
)

print("Descending Drive neurons:")
print(f"\tActive neurons: {len(dd_firing_rates)}/{descending_drive_pool.n}")
if len(dd_firing_rates) > 0:
    print(f"\tMean firing rate: {np.mean(dd_firing_rates):.1f} ± {np.std(dd_firing_rates):.1f} Hz")
    print(f"\tRate range: {np.min(dd_firing_rates):.1f} - {np.max(dd_firing_rates):.1f} Hz")

print("Motor neurons:")
print(f"\tActive neurons: {len(mn_firing_rates)}/{motor_neuron_pool.n}")
if len(mn_firing_rates) > 0:
    print(f"\tMean firing rate: {np.mean(mn_firing_rates):.1f} ± {np.std(mn_firing_rates):.1f} Hz")
    print(f"\tRate range: {np.min(mn_firing_rates):.1f} - {np.max(mn_firing_rates):.1f} Hz")

## Calculate and Save ISI/CV Statistics

Calculate ISI and CV for each motor unit and save to CSV file



In [ ]:
# Calculate ISI/CV statistics for motor neurons
print("\nCalculating ISI and CV statistics...")
print(f"\tAnalyzing only plateau phase: {ramp_up_end:.1f} - {plateau_end:.1f} ms")
isi_cv_df = calculate_firing_rate_statistics(
    mn_segment.spiketrains,
    plateau_start_ms=ramp_up_end,
    plateau_end_ms=plateau_end,
    return_per_neuron=True,
    min_spikes_for_cv=3,
)

# Save ISI/CV statistics to CSV
output_file = RESULTS_DIR / f"{STUDY_PREFIX}isi_cv_data_{MUSCLE_TYPE}_{MVC_LEVEL}.csv"
isi_cv_df.to_csv(output_file, index=False)

print(f"\nSaved ISI/CV data to: {output_file}")
print(f"\tTotal motor units analyzed: {len(isi_cv_df)}")
if len(isi_cv_df) > 0:
    print(f"\tMean firing rate: {isi_cv_df['mean_firing_rate_Hz'].mean():.2f} Hz")
    print(f"\tMean CV: {isi_cv_df['CV_ISI'].mean():.3f}")

## Visualize Drive Pattern and Spike Trains

Create verification plots showing drive input and resulting neural activity.



In [ ]:
print("\nCreating verification plots...")

colors = plt.rcParams["axes.prop_cycle"].by_key()["color"]

# Create figure with 2 subplots
fig, axes = plt.subplots(2, 1, figsize=(14, 10), sharex=True)

# 1. Drive pattern
time_s = trapezoid_drive__signal.times.rescale(pq.s).magnitude
axes[0].plot(time_s, trapezoid_drive__signal, linewidth=2, label="DD Input")
axes[0].axhline(dd_baseline__Hz, linestyle="--", alpha=0.7, label="Baseline")
axes[0].set_ylabel("Drive (Hz)")
axes[0].set_title(
    f"Trapezoidal Drive Pattern (Optimized DD: {DD_PEAK__Hz:.1f} Hz, "
    f"Gamma shape: {DD_SHAPE_PARAMETER:.2f})"
)
axes[0].legend(framealpha=1.0, edgecolor="none")
axes[0].grid(True, alpha=0.3)

# 2. Motor neuron raster plot (recruitment ordered)
mn_colors = plt.cm.get_cmap("Reds")(np.linspace(0.3, 0.9, len(mn_segment.spiketrains)))
active_mn_count = 0
for i, (spiketrain, color) in enumerate(zip(mn_segment.spiketrains, mn_colors)):
    if len(spiketrain) > 0:
        spike_times = spiketrain.rescale(pq.s).magnitude
        axes[1].scatter(spike_times, [i] * len(spike_times), c=[color], s=1.0, alpha=0.8)
        active_mn_count += 1

axes[1].set_xlabel("Time (s)")
axes[1].set_ylabel("Motor Neuron ID\n(Recruitment Order)")
axes[1].set_title(f"Motor Neuron Activity (n={active_mn_count}/{motor_neuron_pool.n} active)")
axes[1].set_ylim(-1, motor_neuron_pool.n)
axes[1].grid(True, alpha=0.3)

# Format all axes
for ax in axes:
    ax.set_xlim(0, simulation_time / 1000.0)

plt.tight_layout()
plt.savefig(
    RESULTS_DIR / f"{STUDY_PREFIX}simulation_verification_{MUSCLE_TYPE}_{MVC_LEVEL}.png",
    dpi=150,
    bbox_inches="tight",
)
plt.show()

## Individual Motor Neuron Discharge Rates

Compute smoothed instantaneous firing rates for each motor neuron
using a Hanning window (similar to 01_simulate_spike_trains_descending_drive.py)



In [ ]:
print("\nComputing smoothed discharge rates per neuron...")

# Smoothing parameters
window_ms = 400  # 400 ms Hanning window
dt_s = TIMESTEP__ms / 1000.0  # simulation timestep in seconds
window_samples = int(window_ms / 1000.0 / dt_s)

# Hanning window normalized to preserve rate
hanning_window = np.hanning(window_samples)
hanning_window = hanning_window / (hanning_window.sum() * dt_s)  # convert to Hz

mn_instantaneous_rates = []
active_neuron_ids = []

for i, spiketrain in enumerate(mn_segment.spiketrains):
    if len(spiketrain) > 2:
        # Convert spike times to a binary spike train
        t = np.arange(0, simulation_time / 1000.0, dt_s)
        spikes = np.zeros_like(t)
        spike_indices = np.searchsorted(t, spiketrain.rescale(pq.s).magnitude)
        spikes[spike_indices[spike_indices < len(t)]] = 1

        # Convolve with Hanning window
        rate = np.convolve(spikes, hanning_window, mode="same")
        mn_instantaneous_rates.append(rate)
        active_neuron_ids.append(i)

print(f"\tComputed rates for {len(active_neuron_ids)} active motor neurons")

# Create figure for discharge rate visualizations
fig2, axes2 = plt.subplots(2, 1, figsize=(15, 10), sharex=True)

# 1. Heatmap of instantaneous firing rates
if len(mn_instantaneous_rates) > 0:
    # Stack rates into 2D array (neurons x time)
    rates_array = np.array(mn_instantaneous_rates)
    time_points_arr = np.linspace(0, simulation_time / 1000.0, rates_array.shape[1])

    # Plot heatmap
    im = axes2[0].imshow(
        rates_array,
        aspect="auto",
        cmap="hot",
        interpolation="bilinear",
        extent=[0, simulation_time / 1000.0, 0, len(active_neuron_ids)],
        origin="lower",
        vmin=0,
        vmax=np.percentile(rates_array, 95),  # Cap at 95th percentile
    )

    axes2[0].set_ylabel("Motor Neuron ID\n(Recruitment Order)")
    axes2[0].set_title(
        f"Individual Motor Neuron Discharge Rates - {MUSCLE_TYPE} @ {MVC_LEVEL}% MVC\n"
        f"(Smoothed with {window_ms}ms Hanning Window)"
    )
    # Add colorbar
    cbar = plt.colorbar(im, ax=axes2[0])
    cbar.set_label("Firing Rate (Hz)")
    axes2[0].grid(False)

    # 2. Individual traces (show all active neurons)
    n_to_plot = len(active_neuron_ids)

    # Use colormap for lines (gradient showing recruitment order)
    colors = plt.cm.get_cmap("rainbow")(np.linspace(0, 1, n_to_plot))

    for neuron_idx in range(n_to_plot):
        axes2[1].plot(
            time_points_arr,
            mn_instantaneous_rates[neuron_idx],
            linewidth=0.8,
            color=colors[neuron_idx],
            label=f"MN {active_neuron_ids[neuron_idx]}" if n_to_plot <= 20 else None,
        )

    axes2[1].set_xlabel("Time (s)")
    axes2[1].set_ylabel("Firing Rate (Hz)")
    axes2[1].set_title(f"All Motor Neuron Discharge Rates (n={n_to_plot})")

    # Only show legend if there are few neurons
    if n_to_plot <= 20:
        axes2[1].legend(loc="upper right", ncol=3, framealpha=1.0, edgecolor="none")

    axes2[1].grid(True, alpha=0.3)
    axes2[1].set_xlim(0, simulation_time / 1000.0)
    axes2[1].set_ylim(0, np.max(rates_array) * 1.1)

plt.tight_layout()
discharge_plot_path = RESULTS_DIR / f"{STUDY_PREFIX}discharge_rates_{MUSCLE_TYPE}_{MVC_LEVEL}.png"
plt.savefig(discharge_plot_path, dpi=150, bbox_inches="tight")
plt.show()

print(f"\nSaved discharge rate plot to: {discharge_plot_path}")